##Pipeline


In [2]:
import pandas as pd
import numpy as np
import spacy
import re
from scipy.spatial import distance
import math
import pickle
import string
import pandas as pd
import numpy as np
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize, sent_tokenize
import nltk
import string
nltk.download('punkt')
nltk.download('stopwords')
# from readability import Readability
#

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Aditya\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping tokenizers\punkt.zip.
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Aditya\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping corpora\stopwords.zip.


True

In [3]:
#********Lexical Features********
# syllable count

def syllable_count(word):
    word = word.lower()
    count = 0
    vowels = "aeiouy"
    if word[0] in vowels:
        count += 1
    for index in range(1, len(word)):
        if word[index] in vowels and word[index - 1] not in vowels:
            count += 1
            if word[index]=='e':
                count -= 1
    if count == 0:
        count += 1
    return count

def avg_syllable_count(text):
    tokens = sent_tokenize(text)
    l1 = [word for token in tokens for word in token.split()]
    print(tokens)
    print(l1)
    # print([syllable_count(word) for word in l1])
    return np.average([syllable_count(word) for word in l1])


#avg word length

def avg_wordlength(text):
    string1 = text.translate(string.punctuation)
    # print(string1)
    tokens = word_tokenize(string1, language='english')
    # print(tokens)
    st = [",", ".", "'", "!", '"', "#", "$", "%", "&", "(", ")", "*", "+", "-", ".", "/", ":", ";", "<", "=", '>', "?",
          "@", "[", "\\", "]", "^", "_", '`', "{", "|", "}", '~', '\t', '\n']
    stop = stopwords.words('english') + st
    words = [word for word in tokens if word not in stop]
    return np.average([len(word) for word in words])


#avg sentence length by number of words

def avg_sentlengthbyword(text):
    tokens = sent_tokenize(text)
    return np.average([len(token.split()) for token in tokens])


def count_functionalwords(text):
    functional_words = """a between in nor some upon
    about both including nothing somebody us
    above but inside of someone used
    after by into off something via
    all can is on such we
    although cos it once than what
    am do its one that whatever
    among down latter onto the when
    an each less opposite their where
    and either like or them whether
    another enough little our these which
    any every lots outside they while
    anybody everybody many over this who
    anyone everyone me own those whoever
    anything everything more past though whom
    are few most per through whose
    around following much plenty till will
    as for must plus to with
    at from my regarding toward within
    be have near same towards without
    because he need several under worth
    before her neither she unless would
    behind him no should unlike yes
    below i nobody since until you
    beside if none so up your
    """

    functional_words = functional_words.split()
    tokens = sent_tokenize(text)
    wo_punc = [text.translate(str.maketrans ('', '', string.punctuation)) for text in tokens]
    l1 = [word for token in wo_punc for word in token.split()]
    count = 0

    for i in l1:
        if i in functional_words:
            count += 1

    return count / len(l1)


#punc count

def punctuation_count_ratio(text):
    st = [",", ".", "'", "!", '"', ";", "?", ":", ";"]
    count = 0
    for i in text:
        if (i in st):
            count = count + 1
    text = text.replace(" ", "")
    # print(text)
    return float(count) / float(len(text))


#********Readability score********
!pip install readability

import readability
#https://github.com/burrsettles/readability/blob/master/readability.py


#*******Semantic spread*******

!pip install spacy
!python -m spacy download en_core_web_md
!python -m spacy download nl_core_news_lg
!pip install spacy-transformers
nlp = spacy.load("en_core_web_md")
# nlp_trf = spacy.load("en_core_web_trf")
nlp_nl = spacy.load("nl_core_news_lg")


def remove_newlines(text):
    cleaned_text = re.sub(r'\n', '', text)
    return cleaned_text


def calculate_semantic_spread(paragraph, lang):
    doc = nlp(paragraph) if lang=="en" else nlp_nl(paragraph)
    sentences = [sent.text for sent in doc.sents]
    # print(sentences)
    spreads = []
    for sentence in sentences:
        sentence_doc = nlp(sentence) if lang=="en" else nlp_nl(sentence)
        # print(sentence_doc)
        vectors = [token.vector for token in sentence_doc]
        # print(vectors)
        similarities = distance.pdist(vectors, metric="cosine")
        # print(similarities)
        spread = np.nanstd(similarities)
        spreads.append(spread)
    return np.nanmean(spreads)

def pos_calculate_semantic_spread(text, lang):
  doc = nlp(text) if lang=="en" else nlp_nl(text)
  sentences = [sent.text for sent in doc.sents]
  # print(sentences)
  len_tokens = len([tok.text for tok in doc if not tok.is_punct])

  spreads = []
  noun_count = 0
  verb_count = 0
  adj_count = 0
  adv_count = 0
  # print(len_tokens)
  if len_tokens <= 1:
        return 0.0

  for sentence in sentences:
    sentence_doc = nlp(sentence) if lang=="en" else nlp_nl(sentence)
    # doc = nlp(text) if lang=="en" else nlp_nl(text)
    for token in sentence_doc:
        if token.pos_ == "NOUN":
            noun_count += 1
        elif token.pos_ == "VERB":
            verb_count += 1
        elif token.pos_ == "ADJ":
            adj_count += 1
        elif token.pos_ == "ADV":
            adv_count += 1
        # print(token, token.similarity(doc))
        # total_similarity += token.similarity(doc)

  # print(noun_count, verb_count, adj_count, adv_count)
  noun_ratio = noun_count / len_tokens
  verb_ratio = verb_count / len_tokens
  adj_ratio = adj_count / len_tokens
  adv_ratio = adv_count / len_tokens

  semantic_spread = (noun_ratio + verb_ratio + adj_ratio + adv_ratio) / 4
  # average_similarity = total_similarity / token_count

  return semantic_spread


#*******Lexical diversity*********
!pip install lexicalrichness
from lexicalrichness import LexicalRichness

  Installing build dependencies: started
  Installing build dependencies: finished with status 'done'
  Getting requirements to build wheel: started
  Getting requirements to build wheel: finished with status 'done'
  Preparing metadata (pyproject.toml): started
  Preparing metadata (pyproject.toml): finished with status 'done'
  Created wheel for readability: filename=readability-0.3.1-py3-none-any.whl size=35493 sha256=c3e5bcc7b7dc8cdcb60f43e3244a45bd7f3401a624ea0355629bf959a8029911
  Stored in directory: c:\users\aditya\appdata\local\pip\cache\wheels\4e\7c\09\fd4dab2933175bd6e6f0fe30f2f1abf3be749c6f68b8c0fa46
Successfully built readability
     ---------------------------------------- 0.0/42.8 MB ? eta -:--:--
     ---------------------------------------- 0.3/42.8 MB 10.9 MB/s eta 0:00:04
      --------------------------------------- 0.7/42.8 MB 7.0 MB/s eta 0:00:07
      --------------------------------------- 1.0/42.8 MB 6.8 MB/s eta 0:00:07
     - --------------------------------

In [4]:
def style_score(text):
  #lexical features
  avg_syllable_count0 = avg_syllable_count(text)
  avg_wordlength0 = avg_wordlength(text)
  avg_sentlengthbyword0 = avg_sentlengthbyword(text)
  count_functionalwords0 = count_functionalwords(text)
  punctuation_count_ratio0 = punctuation_count_ratio(text)

  #readability scores
  results = readability.getmeasures(text, lang='en')
  fleschreadingease = results['readability grades']['FleschReadingEase']
  kincaid = results['readability grades']['Kincaid']
  gunningfogindex = results['readability grades']['GunningFogIndex']
  dalechallindex = results['readability grades']['DaleChallIndex']

  #Vocab richness
  lex = LexicalRichness(text)
  yulek = lex.yulek
  herdan = lex.Herdan
  maas = lex.Maas
  msttr = lex.msttr(segment_window=15)
  mattr = lex.mattr(window_size=15)
  simpsond = lex.simpsond

  #Semantic spread
  sem_spread = calculate_semantic_spread(text, 'en')
  pos_sem_spread = pos_calculate_semantic_spread(text, 'en')

  vector = [avg_syllable_count0, avg_wordlength0, avg_sentlengthbyword0, count_functionalwords0, punctuation_count_ratio0,

            fleschreadingease, kincaid, gunningfogindex, dalechallindex,

            yulek, herdan, maas, msttr, mattr, simpsond,

            sem_spread, pos_sem_spread
            ]

  style_dict = {}
  count = 0
  for metric in ['avg_syllable_count', 'avg_wordlength', 'avg_sentlengthbyword', 'count_functionalwords', 'punctuation_count_ratio', 'fleschreadingease', 'kincaid', 'gunningfogindex', 'dalechallindex', 'yulek', 'herdan', 'maas', 'msttr', 'mattr', 'simpsond','sem_spread', 'pos_sem_spread']:
    style_dict[metric] = vector[count]
    count+=1

  return vector, style_dict

##Data formation

In [9]:
import os
path='annotated dataset with decision'
l = os.listdir('annotated dataset with decision')

In [10]:
texts=[]
for review in l:
    r = os.path.join(path, review)
    with open(r, 'r') as file:
        file_contents = file.read()
    pattern = r"\[\[.*?\]\]|\[.*?\]|\brating:\s*\d+\s*|\bconfidence:\s*\d+\s*"
    cleaned_text = re.sub(pattern, "", file_contents)
    texts.append(cleaned_text)

In [13]:
count=-1
length = []
for text in texts:
  count+=1
  length.append((count,len(word_tokenize(text))))
  print(count, len(word_tokenize(text)))


0 272
1 476
2 862
3 565
4 298
5 481
6 590
7 363
8 730
9 399
10 317
11 666
12 324
13 489
14 182
15 510
16 93
17 861
18 165
19 349
20 443
21 119
22 257
23 685
24 209
25 697
26 287
27 221
28 139
29 234
30 397
31 151
32 477
33 258
34 147
35 248
36 224
37 290
38 925
39 553
40 876
41 518
42 480
43 301
44 393
45 412
46 617
47 123
48 77
49 773
50 1228
51 488
52 203
53 331
54 615
55 399
56 684
57 246
58 524
59 335
60 1050
61 728
62 437
63 388
64 134
65 472
66 60
67 379
68 274
69 633
70 43
71 812
72 931
73 184
74 498
75 666
76 35
77 683
78 236
79 374
80 828
81 126
82 365
83 410
84 549
85 286
86 519
87 658
88 331
89 1141
90 663
91 410
92 92
93 309
94 299
95 636
96 72
97 475
98 297
99 100
100 214
101 301
102 524
103 1042
104 135
105 252
106 741
107 1207
108 824
109 473
110 353
111 113
112 667
113 274
114 226
115 274
116 263
117 401
118 483
119 294
120 872
121 471
122 346
123 283
124 639
125 231
126 511
127 390
128 390
129 154
130 203
131 496
132 418
133 293
134 315
135 606
136 202
137 336
138 979


In [14]:
length.sort(key=lambda a:a[1])

In [15]:
print(length)

[(256, 28), (76, 35), (211, 36), (697, 38), (1203, 41), (70, 43), (635, 46), (1173, 58), (153, 59), (66, 60), (1132, 60), (466, 69), (217, 71), (1119, 71), (96, 72), (602, 72), (48, 77), (405, 78), (508, 86), (1162, 90), (142, 91), (286, 91), (1185, 91), (92, 92), (16, 93), (1197, 93), (649, 94), (575, 98), (402, 99), (830, 99), (1178, 99), (99, 100), (804, 100), (1158, 103), (1086, 104), (426, 107), (443, 107), (927, 107), (1193, 108), (308, 109), (467, 109), (825, 109), (802, 110), (111, 113), (252, 114), (986, 116), (770, 118), (21, 119), (273, 119), (841, 119), (633, 120), (883, 121), (924, 121), (47, 123), (536, 123), (397, 124), (686, 125), (687, 125), (939, 125), (81, 126), (798, 126), (577, 129), (725, 131), (684, 132), (820, 132), (344, 133), (64, 134), (525, 134), (786, 134), (104, 135), (1168, 135), (223, 136), (992, 138), (28, 139), (615, 140), (828, 142), (870, 142), (887, 142), (911, 142), (338, 143), (403, 143), (593, 143), (601, 143), (683, 143), (768, 143), (158, 144),

In [ ]:
for x, y in enumerate(length):
    if y[1] == 19 and y[0]<800:
      print(y)

In [16]:
vectors = []
count=-1
for text in texts:
  count+=1
  print(count)
  vectors.append(style_score(text))

0
['"The idea of using cross-task transfer performance to do task clustering is not new.', 'Please refer to the paper \\u201cDiscovering structure in multiple learning tasks: The TC algorithm\\u201d published in ICML 1996.', 'One issue of the use of cross-task transfer performance to measure task relations is that it ignores the negative correlations between tasks, which is useful for learning from multiple tasks.', 'For example, in binary classification tasks, a very small S_{ij} indicates that by changing the sign of the classification function these two tasks are useful to each other.', 'So the use of cross-task transfer performance and the task clustering approach can only capture positive correlations between tasks but ignore the negative task relations which are also important to the sharing among tasks in multi-task learning.. .', 'Problem (2) is identical to robust PCA and Theorem 3.1 is common in matrix completion literature.', 'I don\\u2019t see much novelty.', 'Appendix A se

c:\users\aditya\appdata\local\programs\python\python38\lib\site-packages\numpy\lib\nanfunctions.py:1872: RuntimeWarning: Degrees of freedom <= 0 for slice.
  var = nanvar(a, axis=axis, dtype=dtype, out=out, ddof=ddof,


7
['"The main contribution of the paper is a method that provides visual explanations of classification decisions.', 'The proposed method uses .', '- a generator trained in a GAN setup.', '- an autoencoder to obtain a latent space representation.', '- a method inspired by adversarial sample generation to obtain a generated image from another class - which can then be compared to the original image (or rather the reconstruction of it).', '.', 'The method is evaluated on a medical images dataset and some additional demonstration on MNIST is provided.. .', '.', '- The paper proposes a (I believe) novel method to obtain visual explanations.', 'The results are visually compelling although most results are shown on a medical dataset - which I feel is very hard for most readers to follow.', 'The MNIST explanations help a lot.', 'It would be great if the authors could come up with an additional way to demonstrate their method to the non-medical reader.. .', '- The paper shows that the results 

c:\users\aditya\appdata\local\programs\python\python38\lib\site-packages\numpy\lib\nanfunctions.py:1872: RuntimeWarning: Degrees of freedom <= 0 for slice.
  var = nanvar(a, axis=axis, dtype=dtype, out=out, ddof=ddof,


51
['"This paper leverages how deep Bayesian NNs, in the limit of infinite width, are Gaussian processes (GPs).', 'After characterizing the kernel function, this allows us to use the GP framework for prediction, model selection, uncertainty estimation, etc.. .', '.', '- Pros of this work.', '.', 'The paper provides a specific method to efficiently compute the covariance matrix of the equivalent GP and shows experimentally on CIFAR and MNIST the benefits of using the this GP as opposed to a finite-width non-Bayesian NN.. .', 'The provided phase analysis and its relation to the depth of the network is also very interesting.. .', 'Both are useful contributions as long as deep wide Bayesian NNs are concerned.', 'A different question is whether that regime is actually useful.. .', '.', '- Cons of this work.', '.', 'Although this work introduces a new GP covariance function inspired by deep wide NNs, I am unconvinced of the usefulness of this regime for the cases in which deep learning is us

...

1176
['"The paper investigates the representation of polynomials by neural networks up to a certain degree and implied uniform approximations.', 'It shows exponential gaps between the width of shallow and deep networks required for approximating a given sparse polynomial.', '.', '.', 'By focusing on polynomials, the paper is able to use of a variety of tools (e.g.', 'linear algebra) to investigate the representation question.', 'Results such as Proposition 3.3 relate the representation of a polynomial up to a certain degree, to the approximation question.', 'Here it would be good to be more specific about the domain, however, as approximating the low order terms certainly does not guarantee a global uniform approximation.', '.', '.', 'Theorem 3.4 makes an interesting claim, that a finite network size is sufficient to achieve the best possible approximation of a polynomial (the proof building on previous results, e.g.', 'by Lin et al that I did not verify).', 'The idea being to construc

c:\users\aditya\appdata\local\programs\python\python38\lib\site-packages\numpy\lib\nanfunctions.py:1872: RuntimeWarning: Degrees of freedom <= 0 for slice.
  var = nanvar(a, axis=axis, dtype=dtype, out=out, ddof=ddof,


1181
['"Summary:.', 'This paper investigated the problem of attribute-conditioned image generation using generative adversarial networks.', 'More specifically, the paper proposed to generate images from attribute and latent code as high-level representation.', 'To learn the mapping from image to high-level representations, an auxiliary encoder was introduced.', 'The model was trained using a combination of reconstruction (auto-encoding) and adversarial loss.', 'To further encourage effective disentangling (against trivial solution), an annihilating operation was proposed together with the proposed training pipeline.', 'Experimental evaluations were conducted on standard face image databases such as Multi-PIE and CelebA.', '.', '.', '== Novelty and Significance ==.', 'Multi-attribute image generation is an interesting task but has been explored to some extent.', 'The integration of generative adversarial networks with auto-encoding loss is not really a novel contribution.', '.', '-- Aut

c:\users\aditya\appdata\local\programs\python\python38\lib\site-packages\numpy\lib\nanfunctions.py:1872: RuntimeWarning: Degrees of freedom <= 0 for slice.
  var = nanvar(a, axis=axis, dtype=dtype, out=out, ddof=ddof,


1193
['"This work exploits the causality principle to quantify how the weights of successive layers adapt to each other.', 'Some interesting results are obtained, such as \\"enforcing more independence between successive layers of generators may lead to better performance and modularity of these architectures\\" .', 'Generally, the result is interesting and the presentation is easy to follow.', 'However, the proposed approach and the experiments are not convincible enough.', 'For example,  it is hard to obtain the conclusion \\"more independence lead to better performance\\" from the experimental results.', 'Maybe more justifications are needed."']
['"This', 'work', 'exploits', 'the', 'causality', 'principle', 'to', 'quantify', 'how', 'the', 'weights', 'of', 'successive', 'layers', 'adapt', 'to', 'each', 'other.', 'Some', 'interesting', 'results', 'are', 'obtained,', 'such', 'as', '\\"enforcing', 'more', 'independence', 'between', 'successive', 'layers', 'of', 'generators', 'may', 'lea

In [17]:
print(vectors[0])

([1.430327868852459, 6.569620253164557, 20.333333333333332, 0.34297520661157027, 0.01896813353566009, -172.2903614457831, 99.1489156626506, 106.025702811245, 23.406297590361447, 146.46600376242947, 0.8826417648262573, 0.02134885278455948, 0.9416666666666668, 0.9336231884057992, 0.014706874451865344, 0.1699173653539634, 0.13438735177865613], {'avg_syllable_count': 1.430327868852459, 'avg_wordlength': 6.569620253164557, 'avg_sentlengthbyword': 20.333333333333332, 'count_functionalwords': 0.34297520661157027, 'punctuation_count_ratio': 0.01896813353566009, 'fleschreadingease': -172.2903614457831, 'kincaid': 99.1489156626506, 'gunningfogindex': 106.025702811245, 'dalechallindex': 23.406297590361447, 'yulek': 146.46600376242947, 'herdan': 0.8826417648262573, 'maas': 0.02134885278455948, 'msttr': 0.9416666666666668, 'mattr': 0.9336231884057992, 'simpsond': 0.014706874451865344, 'sem_spread': 0.1699173653539634, 'pos_sem_spread': 0.13438735177865613})


In [18]:
columns = vectors[0][1].keys()
columns

dict_keys(['avg_syllable_count', 'avg_wordlength', 'avg_sentlengthbyword', 'count_functionalwords', 'punctuation_count_ratio', 'fleschreadingease', 'kincaid', 'gunningfogindex', 'dalechallindex', 'yulek', 'herdan', 'maas', 'msttr', 'mattr', 'simpsond', 'sem_spread', 'pos_sem_spread'])

In [19]:
dict2df={}
count=-1
for column in columns:
  count+=1
  temp = []
  for vector in vectors:
    temp.append(vector[0][count])
  dict2df[column]=temp

In [20]:
print(len(dict2df['avg_syllable_count']))

1204


In [21]:
vector_df = pd.DataFrame(dict2df)

In [22]:
vector_df.head()

avg_syllable_count  avg_wordlength  avg_sentlengthbyword  \
0            1.430328        6.569620             20.333333   
1            1.345771        6.314741             20.100000   
2            1.335072        5.884187             19.175000   
3            1.346723        5.984177             14.333333   
4            1.492308        6.829412             13.684211   

   count_functionalwords  punctuation_count_ratio  fleschreadingease  \
0               0.342975                 0.018968        -172.290361   
1               0.355330                 0.027711        -323.126549   
2               0.403670                 0.027876        -702.123175   
3               0.315436                 0.046006        -381.606316   
4               0.341564                 0.026685        -191.648770   

      kincaid  gunningfogindex  dalechallindex       yulek    herdan  \
0   99.148916       106.025703       23.406298  146.466004  0.882642   
1  156.954861       165.651385       30.685760  115.694813  0.852318   
2  304.468303       316.084319       47.826894  120.398137  0.852871   
3  179.768860       188.540351       34.010591  123.746377  0.885285   
4  100.606885       107.272131       23.504474  149.825316  0.884057   

       maas     msttr     mattr  simpsond  sem_spread  pos_sem_spread  
0  0.021349  0.941667  0.933623  0.014707    0.169917        0.134387  
1  0.024711  0.907692  0.916491  0.011599    0.185623        0.137349  
2  0.022158  0.933333  0.935641  0.012056    0.165170        0.128906  
3  0.018861  0.935632  0.934434  0.012403    0.184355        0.124187  
4  0.021091  0.912500  0.913333  0.015044    0.154460        0.147638

In [23]:
vector_df['text'] = texts

In [24]:
df2 = pd.read_csv('data_latest_final2.csv')

In [26]:
vector_df['informativeness_score'] = df2['informativeness_score']

In [27]:
vector_df.to_csv('ml_models_data.csv')

In [28]:
vector_df.head()

avg_syllable_count  avg_wordlength  avg_sentlengthbyword  \
0            1.430328        6.569620             20.333333   
1            1.345771        6.314741             20.100000   
2            1.335072        5.884187             19.175000   
3            1.346723        5.984177             14.333333   
4            1.492308        6.829412             13.684211   

   count_functionalwords  punctuation_count_ratio  fleschreadingease  \
0               0.342975                 0.018968        -172.290361   
1               0.355330                 0.027711        -323.126549   
2               0.403670                 0.027876        -702.123175   
3               0.315436                 0.046006        -381.606316   
4               0.341564                 0.026685        -191.648770   

      kincaid  gunningfogindex  dalechallindex       yulek    herdan  \
0   99.148916       106.025703       23.406298  146.466004  0.882642   
1  156.954861       165.651385       30.685760  115.694813  0.852318   
2  304.468303       316.084319       47.826894  120.398137  0.852871   
3  179.768860       188.540351       34.010591  123.746377  0.885285   
4  100.606885       107.272131       23.504474  149.825316  0.884057   

       maas     msttr     mattr  simpsond  sem_spread  pos_sem_spread  \
0  0.021349  0.941667  0.933623  0.014707    0.169917        0.134387   
1  0.024711  0.907692  0.916491  0.011599    0.185623        0.137349   
2  0.022158  0.933333  0.935641  0.012056    0.165170        0.128906   
3  0.018861  0.935632  0.934434  0.012403    0.184355        0.124187   
4  0.021091  0.912500  0.913333  0.015044    0.154460        0.147638   

                                                text  informativeness_score  
0  "The idea of using cross-task transfer perform...               0.459268  
1  "This paper proposes a method for multitask an...               0.705510  
2  "The authors propose techniques for multitask ...               0.766092  
3  ". Summary: . - This paper proposes a hand-des...               0.862081  
4  "Summary.  - This paper mainly focuses on a co...               0.802641